# Req

In [ ]:
!pip install lightfm

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 316.4/316.4 kB 4.6 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Created wheel for lightfm: filename=lightfm-1.17-cp310-cp310-linux_x86_64.whl size=808332 sha256=11eca225dad0e5304e6092339c7b87850c2c4bfc1c5adbb186107d48a43025e1
  Stored in directory: /root/.cache/pip/wheels/4f/9b/7e/0b256f2168511d8fa4dae4fae0200fdbd729eb424a912ad636
Successfully built lightfm


# sistem rekomendasi

In [ ]:
import pandas as pd
from sklearn.preprocessing import LabelEncoder
from gensim.models import Word2Vec
from lightfm import LightFM
from lightfm.data import Dataset as LightFMDataset
from scipy.sparse import coo_matrix
from scipy.sparse import csr_matrix
from sklearn.metrics import mean_absolute_error, mean_squared_error
import numpy as np
import pickle
import joblib

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
data = pd.read_csv('/content/drive/MyDrive/Colab_Notebooks/Dataset_asuransi/data_after_all_training.csv')

In [ ]:
data.head()

username                                          full_text Produk  \
0       Ditanyadia  shintaaraa 15 jt per tahun sist bukan kantor s...    AIA   
1  MuhTaufikRahmat  kumpar mohon klarifikasi dr pihak asuransi ada...    AIA   
2    fiona99351131  aia aia indonesia asuransi unit link 5 tips se...    AIA   
3          fiayeee  rikici halo bang maaf nimbrung boleh saya dm k...    AIA   
4   vivian89043067  aia aia indonesia asuransi unit link 5 tips se...    AIA   

   produk_id  user_id  rating predicted_product  
0          0      168       5               AIA  
1          0      376       1          Manulife  
2          0     1059       5               AIA  
3          0     1055       3               AIA  
4          0     1890       5               AIA

In [ ]:
data.drop(['predicted_product'], axis=1, inplace=True)

In [ ]:
data.head()

username                                          full_text Produk  \
0       Ditanyadia  shintaaraa 15 jt per tahun sist bukan kantor s...    AIA   
1  MuhTaufikRahmat  kumpar mohon klarifikasi dr pihak asuransi ada...    AIA   
2    fiona99351131  aia aia indonesia asuransi unit link 5 tips se...    AIA   
3          fiayeee  rikici halo bang maaf nimbrung boleh saya dm k...    AIA   
4   vivian89043067  aia aia indonesia asuransi unit link 5 tips se...    AIA   

   produk_id  user_id  rating  
0          0      168       5  
1          0      376       1  
2          0     1059       5  
3          0     1055       3  
4          0     1890       5

## Word2vec

In [ ]:
# Tokenisasi kalimat ulasan
sentences = [review.split() for review in data['full_text']]

In [ ]:
sentences

[['shintaaraa',
  '15',
  'jt',
  'per',
  'tahun',
  'sist',
  'bukan',
  'kantor',
  'sih',
  'jatuh',
  'nya',
  'dr',
  'asuransi',
  'aia',
  'bpjs',
  'juga',
  'ada',
  'tapi',
  'jumlah',
  'lebih',
  'kecil',
  'lupa',
  'besar',
  'brpa',
  'nggk',
  'pernah',
  'pakai',
  'soal',
  'kalo',
  'dr',
  'kantor',
  'sndiri',
  'ngk',
  'ada',
  'kak'],
 ['kumpar',
  'mohon',
  'klarifikasi',
  'dr',
  'pihak',
  'asuransi',
  'adakamipinjolonlineloanloanscartelfraud',
  'ccsbilifenationwidenationwidenewyorklifeamfamaxaindonesiaaxatherealaiaacaasuransijiwasrayaassinarmaskppuylkiidtulusabadituluswijanarkoingnewsftfsajapan'],
 ['aia',
  'aia',
  'indonesia',
  'asuransi',
  'unit',
  'link',
  '5',
  'tips',
  'selfhealing',
  'untuk',
  'jaga',
  'sehat',
  'mental',
  'product6',
  'bagaimana',
  'produk',
  'unit',
  'link',
  'terus',
  'tumbuh',
  'khusus',
  'di',
  'masa',
  'pandemi',
  'yuk',
  'simak',
  'apa',
  'kata',
  'prita',
  'ghozi',
  'kena',
  'tingkat',
  'per

In [ ]:
word2vec_model = Word2Vec(sentences, vector_size=100, window=5, min_count=1, workers=4)

In [ ]:
def average_word_vectors(words, model, vocab, num_features):
    feature_vector = np.zeros((num_features,), dtype='float32')
    n_words = 0

    for word in words:
        if word in vocab:
            n_words += 1
            feature_vector = np.add(feature_vector, model.wv[word])

    if n_words > 0:
        feature_vector = np.divide(feature_vector, n_words)

    return feature_vector

In [ ]:
# Menambahkan vektor rata-rata ke dataset
data['review_vector'] = data['full_text'].apply(lambda x: average_word_vectors(x.split(), word2vec_model, word2vec_model.wv.key_to_index, 100))

In [ ]:
data.head()

username                                          full_text Produk  \
0       Ditanyadia  shintaaraa 15 jt per tahun sist bukan kantor s...    AIA   
1  MuhTaufikRahmat  kumpar mohon klarifikasi dr pihak asuransi ada...    AIA   
2    fiona99351131  aia aia indonesia asuransi unit link 5 tips se...    AIA   
3          fiayeee  rikici halo bang maaf nimbrung boleh saya dm k...    AIA   
4   vivian89043067  aia aia indonesia asuransi unit link 5 tips se...    AIA   

   produk_id  user_id  rating  \
0          0      168       5   
1          0      376       1   
2          0     1059       5   
3          0     1055       3   
4          0     1890       5   

                                       review_vector  
0  [-0.15208568, 0.45652217, -0.12457793, 0.27275...  
1  [-0.15435737, 0.3039457, -0.0737816, 0.1782842...  
2  [-0.18478927, 0.39569104, -0.10744416, 0.22437...  
3  [-0.18487467, 0.43248367, -0.17402788, 0.29788...  
4  [-0.1846632, 0.39532822, -0.107717685, 0.22432...

In [ ]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4416 entries, 0 to 4415
Data columns (total 7 columns):
 #   Column         Non-Null Count  Dtype 
---  ------         --------------  ----- 
 0   username       4416 non-null   object
 1   full_text      4416 non-null   object
 2   Produk         4416 non-null   object
 3   produk_id      4416 non-null   int64 
 4   user_id        4416 non-null   int64 
 5   rating         4416 non-null   int64 
 6   review_vector  4416 non-null   object
dtypes: int64(3), object(4)
memory usage: 241.6+ KB


In [ ]:
def vector_to_string(vector):
    return ' '.join(map(str, vector))

data['review_vector_str'] = data['review_vector'].apply(vector_to_string)

In [ ]:
data.head()

username                                          full_text Produk  \
0       Ditanyadia  shintaaraa 15 jt per tahun sist bukan kantor s...    AIA   
1  MuhTaufikRahmat  kumpar mohon klarifikasi dr pihak asuransi ada...    AIA   
2    fiona99351131  aia aia indonesia asuransi unit link 5 tips se...    AIA   
3          fiayeee  rikici halo bang maaf nimbrung boleh saya dm k...    AIA   
4   vivian89043067  aia aia indonesia asuransi unit link 5 tips se...    AIA   

   produk_id  user_id  rating  \
0          0      168       5   
1          0      376       1   
2          0     1059       5   
3          0     1055       3   
4          0     1890       5   

                                       review_vector  \
0  [-0.15208568, 0.45652217, -0.12457793, 0.27275...   
1  [-0.15435737, 0.3039457, -0.0737816, 0.1782842...   
2  [-0.18478927, 0.39569104, -0.10744416, 0.22437...   
3  [-0.18487467, 0.43248367, -0.17402788, 0.29788...   
4  [-0.1846632, 0.39532822, -0.107717685, 0.22432...   

                                   review_vector_str  
0  -0.15208568 0.45652217 -0.12457793 0.27275556 ...  
1  -0.15435737 0.3039457 -0.0737816 0.17828421 0....  
2  -0.18478927 0.39569104 -0.10744416 0.2243705 0...  
3  -0.18487467 0.43248367 -0.17402788 0.29788116 ...  
4  -0.1846632 0.39532822 -0.107717685 0.22432306 ...

In [ ]:
# Periksa jumlah interaksi per pengguna
print(data.groupby('user_id').size())

# Periksa jumlah interaksi per item
print(data.groupby('produk_id').size())

user_id
0       1
1       2
2       1
3       1
4       1
       ..
1971    1
1972    1
1973    1
1974    1
1975    1
Length: 1928, dtype: int64
produk_id
0    260
1    587
2    552
3    205
4    833
5    748
6    355
7    876
dtype: int64


## LightFM

In [ ]:
# Buat dataset LightFM
lightfm_dataset = LightFMDataset()

In [ ]:
# Fit dataset
lightfm_dataset.fit(
    users=(x for x in data['user_id']),
    items=(x for x in data['produk_id']),
    item_features=(f'vector_{i}' for i in range(100))
)

In [ ]:
# Membuat matrix interaksi
(interactions, weights) = lightfm_dataset.build_interactions(
    ((row['user_id'], row['produk_id'], 1) for idx, row in data.iterrows())
)

In [ ]:
item_features_list = [(row['produk_id'], [f'vector_{i}' for i in range(100)]) for idx, row in data.iterrows()]
item_features = lightfm_dataset.build_item_features((item, features) for item, features in item_features_list)

In [ ]:
item_features_list

[(0,
  ['vector_0',
   'vector_1',
   'vector_2',
   'vector_3',
   'vector_4',
   'vector_5',
   'vector_6',
   'vector_7',
   'vector_8',
   'vector_9',
   'vector_10',
   'vector_11',
   'vector_12',
   'vector_13',
   'vector_14',
   'vector_15',
   'vector_16',
   'vector_17',
   'vector_18',
   'vector_19',
   'vector_20',
   'vector_21',
   'vector_22',
   'vector_23',
   'vector_24',
   'vector_25',
   'vector_26',
   'vector_27',
   'vector_28',
   'vector_29',
   'vector_30',
   'vector_31',
   'vector_32',
   'vector_33',
   'vector_34',
   'vector_35',
   'vector_36',
   'vector_37',
   'vector_38',
   'vector_39',
   'vector_40',
   'vector_41',
   'vector_42',
   'vector_43',
   'vector_44',
   'vector_45',
   'vector_46',
   'vector_47',
   'vector_48',
   'vector_49',
   'vector_50',
   'vector_51',
   'vector_52',
   'vector_53',
   'vector_54',
   'vector_55',
   'vector_56',
   'vector_57',
   'vector_58',
   'vector_59',
   'vector_60',
   'vector_61',
   'vector_62

In [ ]:
# Menambahkan fitur item ke dataset
item_features_list = []
for idx, row in data.iterrows():
    item_features_list.append((row['produk_id'], [row['review_vector_str']]))

In [ ]:
# Memetakan fitur item
unique_features = {feature for item, features in item_features_list for feature in features}
lightfm_dataset.fit_partial(
    items=(x for x in data['produk_id']),
    item_features=unique_features
)

In [ ]:
item_features = lightfm_dataset.build_item_features(
    (item, features) for item, features in item_features_list
)

In [ ]:
# Debugging tambahan: Periksa bentuk dan tipe data
print(f'interactions shape: {interactions.shape}')
print(f'interactions: {interactions}')
print(f'item_features shape: {item_features.shape}')
print(f'item_features: {item_features}')

interactions shape: (1928, 8)
interactions:   (0, 0)	1.0
  (1, 0)	1.0
  (2, 0)	1.0
  (3, 0)	1.0
  (4, 0)	1.0
  (5, 0)	1.0
  (6, 0)	1.0
  (4, 0)	1.0
  (6, 0)	1.0
  (6, 0)	1.0
  (4, 0)	1.0
  (6, 0)	1.0
  (6, 0)	1.0
  (7, 0)	1.0
  (8, 0)	1.0
  (9, 0)	1.0
  (10, 0)	1.0
  (10, 0)	1.0
  (11, 0)	1.0
  (12, 0)	1.0
  (6, 0)	1.0
  (13, 0)	1.0
  (13, 0)	1.0
  (13, 0)	1.0
  (13, 0)	1.0
  :	:
  (1914, 7)	1.0
  (1863, 7)	1.0
  (1915, 7)	1.0
  (1915, 7)	1.0
  (1916, 7)	1.0
  (1603, 7)	1.0
  (1917, 7)	1.0
  (1728, 7)	1.0
  (1603, 7)	1.0
  (1918, 7)	1.0
  (1919, 7)	1.0
  (1920, 7)	1.0
  (1921, 7)	1.0
  (1922, 7)	1.0
  (1603, 7)	1.0
  (6, 7)	1.0
  (1923, 7)	1.0
  (1924, 7)	1.0
  (1925, 7)	1.0
  (1603, 7)	1.0
  (1926, 7)	1.0
  (1926, 7)	1.0
  (1562, 7)	1.0
  (1927, 7)	1.0
  (1603, 7)	1.0
item_features shape: (8, 4356)
item_features:   (0, 0)	0.0038314175
  (0, 30)	0.0038314175
  (0, 54)	0.0038314175
  (0, 59)	0.0038314175
  (0, 78)	0.0038314175
  (0, 83)	0.0038314175
  (0, 93)	0.0038314175
  (0, 112)	0.0

In [ ]:
# Latih model
model = LightFM(loss='warp')
model.fit(interactions, item_features=item_features, epochs=30, num_threads=4)

In [ ]:
# Fungsi untuk mendapatkan rekomendasi
def get_lightfm_recommendations(user_id, model, lightfm_dataset, num_recommendations=5):
    n_users, n_items = interactions.shape
    scores = model.predict(user_id, np.arange(n_items), item_features=item_features)
    top_items = np.argsort(-scores)[:num_recommendations]

    return top_items

In [ ]:
# Contoh mendapatkan rekomendasi untuk pengguna
user_id = 1
recommendations = get_lightfm_recommendations(user_id, model, lightfm_dataset, num_recommendations=5)
print(recommendations)

[7 6 4 2 5]


## Evaluasi

In [ ]:
from lightfm.evaluation import precision_at_k, auc_score

In [ ]:
# Evaluasi model
precision = precision_at_k(model, interactions, item_features=item_features, k=5).mean()
auc = auc_score(model, interactions, item_features=item_features).mean()

In [ ]:
print(f'Precision@5: {precision}')
print(f'AUC: {auc}')

Precision@5: 0.2158714085817337
AUC: nan


In [ ]:
def evaluate_lightfm(model, interactions, lightfm_dataset, item_features):
    user_ids, item_ids = interactions.nonzero()
    actual_ratings = []
    predicted_ratings = []

    for user_id, item_id in zip(user_ids, item_ids):
        actual_rating = interactions.getrow(user_id).toarray()[0, item_id]
        predicted_rating = model.predict(user_id, item_id, item_features=item_features)

        actual_ratings.append(actual_rating)
        predicted_ratings.append(predicted_rating)

    mae = mean_absolute_error(actual_ratings, predicted_ratings)
    rmse = np.sqrt(mean_squared_error(actual_ratings, predicted_ratings))

    return mae, rmse

In [ ]:
# Evaluasi model
precision = precision_at_k(model, interactions, item_features=item_features, k=5).mean()
auc = auc_score(model, interactions, item_features=item_features).mean()


TypeError: object of type 'numpy.int32' has no len()